In [1]:
import os, shutil,pathlib,exifread
r"""Sorting out the raw images collected from camera trap data
Loop through each location and subsequent feed type and images by extracting
the original date the image taken using exifread."""

"""
/test_data
    - C2
    - C3
            - fat_balls
        - standard_seed
        - sunflower_seed
            - date ## This folder is created in this cell
                - 2022_11_23 ## images capture date is extracted saving the image into a seperate folder into the date/raw_images folder
                    - cropped_images ## Images are then cropped using megadetector
                    - raw_images ## This folder temporarily stores raw images before they are cropped by megadetector
            - raw_images ## Contains the folders of raw images
                - 100EK113 ## Images from camera traps are stored in this folder
    - C4
"""
# Define a working directory pathway 
cwd = pathlib.Path("test_data")

# Loop through each folder within the working direcory
for location in os.listdir(cwd):
    
    # Define new file pathway.  
    location_dir = cwd/location 
    
    # Loop through next set of folders 
    for feed_type in os.listdir(location_dir):
        
        # Define new folder paths to be used 
        feed_type_dir = location_dir/feed_type
        image_folder_dir = feed_type_dir/"raw_images"
        
        # Loop through all of folders containing the camera-trap images
        for cameratrap_folder in os.listdir(image_folder_dir):
            
            # Loop though each of the image
            for image in os.listdir(image_folder_dir/cameratrap_folder):
                
                # Corrupted files or invalid file types to be passed
                try: 
                    """Using try/except will pass through corrupt images or files that
                    do not have an exif data to extract"""
                    
                    # Create a image file path to the camera trap image 
                    exif_file = str(feed_type_dir/"raw_images"/cameratrap_folder/image) 
                    img_file = open(exif_file,"rb")
                    tags = exifread.process_file(img_file)
                    """Extract the tags embedded within the image, in this case the Date and time of original image, for this 
                    scenario we are only looking for the date so we can extract from within a string just the date and save 
                    this into a new variable"""
                    
                    date_of_image = str(tags["EXIF DateTimeOriginal"])
                    day_of_image = str(date_of_image[0:10])
                    
                    #Replace the : with _ as it will be easier to open at a later point.
                    date = day_of_image.replace(":","_") 
                    
                    # Define the new file location path for each of the images to be copied to
                    newpath1 = feed_type_dir/"date"/date/"raw_images"
                    img_file.close()
                    
                    """Check if there is a directory already set up in the folder directory, if there isn't a new folder will be
                    made. The image is then checked to prevent any duplication if it has already been copied before"""
                    if not os.path.exists(newpath1):
                        os.makedirs(newpath1)
                    dated_image_path = newpath1/image
                    if not os.path.exists(dated_image_path):
                        shutil.copy(exif_file,dated_image_path)
                except:
                    pass       

FileNotFoundError: [WinError 3] The system cannot find the path specified: 'test_data\\C2\\fat_balls\\raw_images'

In [2]:
# Loop through the directory and use megadetector to detect animals and crop bounding boxes to save into a new directory. 
import os, shutil,pathlib,exifread

# Define the root file pathway 
cwd = pathlib.Path("test_data")

#After each loop a the new folder path is saved into a new variable to make looping more tidy
for location in os.listdir(cwd):
    
    # Define new folder pathway to loop through 
    feed_type_dir = cwd/location
    for feed_type in os.listdir(feed_type_dir):
        
        # Define file pathway for folders for each date
        date_dir = feed_type_dir/feed_type/"date"
        
        # Loop through the dates folders 
        for date in os.listdir(date_dir):
            try:
                ## Define the arguments needed to pass into run_batch_detector and the subsequent crop_detections,
                # the required arguments can be found in the comments inside the files.
                raw_images_dir = str(os.path.abspath(date_dir/date/"raw_images"))
                output_file_path = str(os.path.abspath(date_dir/date/"run_batch_detector_output.json"))
                cropped_image_output_dir = str(os.path.abspath(date_dir/date/"cropped_images"))
                
                # Check if a directory for cropped_image_output has already been created and create one if not 
                if not os.path.exists(cropped_image_output_dir):
                    os.makedirs(cropped_image_output_dir)
                    
                # Check if a directory for .json logs files has already been created and create one if not
                log_dir = os.path.abspath(pathlib.Path("crop_log"))
                if not os.path.exists(log_dir):
                    os.makedirs(log_dir)
                    
                """Run run_batch_detector.py with the args: --megadetector file location, --images directory, --output directory for .json files"""
                %run "C:/git/cameratraps/detection/run_detector_batch.py" "C:/megadetector/md_v5a.0.0.pt" "$raw_images_dir" "$output_file_path" --recursive --output_relative_filenames --threshold 0.8
                
                """Run crop_detections.py with the args: --.json file directory, --image output directory"""
                %run "c:/git/cameratraps/classification/crop_detections.py" "$output_file_path" "$cropped_image_output_dir" --images-dir "$raw_images_dir" --square-crops --logdir "$log_dir"
                
                # Delete the .json file storing the bounding box data to reduce file cluttering
                os.remove(output_file_path)
                
                # remove raw images in the dates folder to reduce directory memory size
                for image in os.listdir(raw_images_dir):
                    
                    # Define the file path for the raw image
                    dirs = os.path.abspath(pathlib.Path(date_dir/date/"raw_images"/image))
                    
                    # Delete the file
                    os.remove(dirs)
                    
                    # Print which file has been deleted
                    print(image, " Deleted")
            except:
                pass
            print("")
        print("")
    print("")

0 image files found in the input directory


AssertionError: Specified image_file does not point to valid image files

FileNotFoundError: [Errno 2] No such file or directory: 'C:\\Users\\vince\\Documents\\BIO3199 Project\\Python\\data\\C2\\fat_balls\\date\\2022_11_13\\run_batch_detector_output.json'


0 image files found in the input directory


AssertionError: Specified image_file does not point to valid image files

...

Finished inference for 3 images in 1.51 seconds
Output file saved at C:\Users\vince\Documents\BIO3199 Project\Python\data\C4\sunflower_seed\date\2023_01_02\run_batch_detector_output.json
Done!
Getting bbox info for 3 images...


100%|████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<?, ?it/s]


Reading/downloading 3 images and cropping...


100%|████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<?, ?it/s]

Downloaded 0 images.
Made 0 new crops.
0 images failed to download or crop.
01020394.JPG  Deleted
01020395.JPG  Deleted
01020396.JPG  Deleted



